In [2]:
# Library imports
import cadquery as cq

In [2]:
# Set variables
base_height=50
base_width= 200
base_length= 100
wall_thickness = 5
rounded_edges= True
screws = True
screw_radius=1
corner_radius=5

In [3]:
# Generate bottom of base
bottom_base=cq.Workplane().rect(base_width, base_length).extrude(base_height)
inner_base=cq.Workplane().rect(base_width-(wall_thickness*2), base_length-(wall_thickness*2)).extrude(base_height-(wall_thickness*2))
bottom_base=bottom_base.cut(inner_base)
bottom_base

In [4]:
# Add rounded edges
if rounded_edges:
    bottom_base=bottom_base.fillet(2)
bottom_base

In [5]:
# Add corners for screw/plugs
corner=cq.Workplane().circle(corner_radius).extrude(base_height - wall_thickness)
positions = [
    (-(base_width/2 - (wall_thickness + corner_radius)), -(base_length/2 - (wall_thickness + corner_radius)),wall_thickness),
    (-(base_width/2 - (wall_thickness + corner_radius)), base_length/2 - (wall_thickness + corner_radius),wall_thickness),
    (base_width/2 - (wall_thickness + corner_radius), -(base_length/2 - (wall_thickness + corner_radius)),wall_thickness),
    (base_width/2 - (wall_thickness + corner_radius), base_length/2 - (wall_thickness + corner_radius),wall_thickness)
]
corners = cq.Workplane()
for pos in positions:
    corners = corners.union(corner.translate(pos))
bottom_base=bottom_base.union(corners)
bottom_base

In [6]:
# Add the screw holes or slots
corner_holes = cq.Workplane()
if screws:
    corner_hole=cq.Workplane().circle(screw_radius).extrude(base_height-(wall_thickness*2))
else:
    corner_hole=cq.Workplane().circle(corner_radius/2).extrude(wall_thickness)
for pos in positions:
    corner_holes=corner_holes.union(corner_hole.translate(pos))
bottom_base=bottom_base.cut(corner_holes)
bottom_base

In [7]:
# Create top base
top_base=cq.Workplane().rect(base_width-(wall_thickness*2), base_length-(wall_thickness*2)).extrude(wall_thickness)
top_base

In [8]:
# Add rounded edges
if rounded_edges:
    top_base=top_base.fillet(2)
top_base

In [9]:
# Add the screw holes or slots
if screws:
    top_base=top_base.cut(corner_holes.translate((0,0,-wall_thickness)))
else:
    top_base=top_base.union(corner_holes.translate((0,0,0)))
top_base

In [10]:
# Create an assembly of the full base
base = cq.Assembly().add(top_base).add(bottom_base, loc=cq.Location((0, base_length, 0)))
base